## Cum am incercat sa minimizez functia de loss
1. Am observat ca algoritmul nu prea converge. Motiv pentru care m-am gandit ca poate sa fie de la cum este compusa reteaua sau de la learning rate.

-> am gasit un learning rate potrivit

-> am modificat layere-le retelei

2. Am testat impactul pe care il are lr variabil si mi-am dat seama ca este unul negativ

-> l-am sters

3. Am inceput sa modific batch size-ul.

-> aici consider ca cerinta "Vedeti daca reusiti sa ajungeti la loss=0 sau loss=0.ceva în urma antrenarii" este putin ambigua. Loss 0.ceva pe batch? pe batch de cate elemente?


Am inceput sa testez loss-ul. Functia de loss insumeaza toate loss-urile din batch. Am incercat sa folosesc o functie de loss care face media si am testat sa vad care este mai potrivita. Am considerat ca referinta loss-ul mediu pe element adica
loss_ref = loss/ batch_size


De acolo am cautat batch size-ul care sa dea cel mai bun rezultat din acest punct de vedere.
In privinta aducerea loss-ului la 0, este de ajuns sa se foloseasca un criterion cu mean, dat fiind ca datele sunt intre 0 si 1 nu poate depasii 1. Daca se foloseste loss-ul cu suma, atunci cu cat batch size-ul este mai mic, cu atat loss-ul va parea mai mic. 


Pana la urma am folosit functia de loss care insumeaza, loss-ul total pe batch de 16 fiind 1.9 -> loss-ul mediu pe predictie = 0.11


In [1]:
from torch.utils.data import Dataset, DataLoader
from torch import nn, from_numpy, optim
import numpy as np

import pandas as pd
import torch
import torch.nn as nn

In [2]:
df=pd.read_csv("diabetes.csv",header=None)

In [3]:
df.values

array([[-0.294118 ,  0.487437 ,  0.180328 , ..., -0.53117  , -0.0333333,
         0.       ],
       [-0.882353 , -0.145729 ,  0.0819672, ..., -0.766866 , -0.666667 ,
         1.       ],
       [-0.0588235,  0.839196 ,  0.0491803, ..., -0.492741 , -0.633333 ,
         0.       ],
       ...,
       [-0.411765 ,  0.21608  ,  0.180328 , ..., -0.857387 , -0.7      ,
         1.       ],
       [-0.882353 ,  0.266332 , -0.0163934, ..., -0.768574 , -0.133333 ,
         0.       ],
       [-0.882353 , -0.0653266,  0.147541 , ..., -0.797609 , -0.933333 ,
         1.       ]])

In [4]:
#Dataset - o clasă din PyTorch foarte utilă gestionării seturilor de date
class DiabetesDataset(Dataset):
    """ Diabetes dataset."""
    # Initialize your data, download, etc.
    def __init__(self):
        #Citim setul de date
        df=pd.read_csv("diabetes.csv",header=None, dtype=np.float32)
        xy = torch.from_numpy(df.values)
        self.len = xy.shape[0]
        #Vom folosi ca input toate valorile mai puțin ultima coloană
        self.x_data = xy[:, 0:-1]
        #Vom folosi ca output ultima coloană
        self.y_data = xy[:, [-1]]

    def __getitem__(self, index):
        return self.x_data[index], self.y_data[index]

    def __len__(self):
        return self.len

In [5]:
dataset = DiabetesDataset()
#DataLoader - un utilitar ce ne ajută să împărțim setul de date pe batch-uri și astfel să facem antrenare în mod Mini-Batch
train_loader = DataLoader(dataset=dataset,
                          batch_size=16,
                          shuffle=True,
                          num_workers=1)

In [6]:
dataset[0]
dataset.len

759

In [8]:

class Model(nn.Module):

    def __init__(self):
        """
        Dat fiind faptul că 
        """
        super(Model, self).__init__()
        torch.manual_seed(0)
        #Practic toate functiile liniare și non-liniare realizează o secvență a flowlui de date
        self.sequential=nn.Sequential(
            nn.Linear(8,12),
            nn.Sigmoid(),
            nn.Linear(12,8),
            nn.Sigmoid(),
            nn.Linear(8,1),
            nn.Sigmoid()
        )

    def forward(self, x):
        return self.sequential(x)

In [9]:
model=Model()

In [10]:
criterion = nn.BCELoss(reduction='mean')
criterion2 = nn.BCELoss(reduction='sum')
optimizer = optim.SGD(model.parameters(), lr=0.08)

In [11]:
# Training loop
for epoch in range(3000):
  #Aplicăm modificarea de learning rate per epocă, deci va trebui să avem un istoric al loss-ului
  losses=[]
  for i, data in enumerate(train_loader, 0):
      # get the inputs
      inputs, labels = data

      # Forward pass: Compute predicted y by passing x to the model
      y_pred = model(inputs)

      # Compute and print loss
      loss = criterion(y_pred, labels)
      loss2 = criterion2(y_pred, labels)  
      print(f'Epoch {epoch + 1} | Batch: {i+1} | Loss: {loss2.item():.4f}')
      losses.append(loss2.item())
      # Zero gradients, perform a backward pass, and update the weights.
      optimizer.zero_grad()
      loss2.backward()
      optimizer.step()
  #if epoch % 100 == 0:
  mean_loss=sum(losses)/len(losses)
  print(f'Mean {mean_loss}')  
  #scheduler.step(mean_loss)

Epoch 1 | Batch: 1 | Loss: 10.9848
Epoch 1 | Batch: 2 | Loss: 11.4577
Epoch 1 | Batch: 3 | Loss: 10.7488
Epoch 1 | Batch: 4 | Loss: 10.5875
Epoch 1 | Batch: 5 | Loss: 11.0917
Epoch 1 | Batch: 6 | Loss: 11.5121
Epoch 1 | Batch: 7 | Loss: 11.8095
Epoch 1 | Batch: 8 | Loss: 9.2981
Epoch 1 | Batch: 9 | Loss: 10.0082
Epoch 1 | Batch: 10 | Loss: 9.9606
Epoch 1 | Batch: 11 | Loss: 8.3549
Epoch 1 | Batch: 12 | Loss: 6.5201
Epoch 1 | Batch: 13 | Loss: 14.2590
Epoch 1 | Batch: 14 | Loss: 11.7500
Epoch 1 | Batch: 15 | Loss: 10.7305
Epoch 1 | Batch: 16 | Loss: 12.3409
Epoch 1 | Batch: 17 | Loss: 10.1577
Epoch 1 | Batch: 18 | Loss: 10.6646
Epoch 1 | Batch: 19 | Loss: 8.9389
Epoch 1 | Batch: 20 | Loss: 11.3391
Epoch 1 | Batch: 21 | Loss: 10.6464
Epoch 1 | Batch: 22 | Loss: 8.9472
Epoch 1 | Batch: 23 | Loss: 15.9881
Epoch 1 | Batch: 24 | Loss: 11.7914
Epoch 1 | Batch: 25 | Loss: 7.6237
Epoch 1 | Batch: 26 | Loss: 9.1184
Epoch 1 | Batch: 27 | Loss: 11.4749
Epoch 1 | Batch: 28 | Loss: 13.6131
Epoch 1 |

Epoch 6 | Batch: 1 | Loss: 9.1617
Epoch 6 | Batch: 2 | Loss: 10.8102
Epoch 6 | Batch: 3 | Loss: 9.1984
Epoch 6 | Batch: 4 | Loss: 11.6590
Epoch 6 | Batch: 5 | Loss: 10.6071
Epoch 6 | Batch: 6 | Loss: 8.8621
Epoch 6 | Batch: 7 | Loss: 12.5726
Epoch 6 | Batch: 8 | Loss: 9.5393
Epoch 6 | Batch: 9 | Loss: 9.9375
Epoch 6 | Batch: 10 | Loss: 9.9190
Epoch 6 | Batch: 11 | Loss: 10.6545
Epoch 6 | Batch: 12 | Loss: 10.6024
Epoch 6 | Batch: 13 | Loss: 9.9598
Epoch 6 | Batch: 14 | Loss: 8.5543
Epoch 6 | Batch: 15 | Loss: 7.1000
Epoch 6 | Batch: 16 | Loss: 7.7599
Epoch 6 | Batch: 17 | Loss: 15.5444
Epoch 6 | Batch: 18 | Loss: 11.2490
Epoch 6 | Batch: 19 | Loss: 10.0351
Epoch 6 | Batch: 20 | Loss: 10.5241
Epoch 6 | Batch: 21 | Loss: 9.9871
Epoch 6 | Batch: 22 | Loss: 9.2705
Epoch 6 | Batch: 23 | Loss: 13.2046
Epoch 6 | Batch: 24 | Loss: 9.9061
Epoch 6 | Batch: 25 | Loss: 7.3632
Epoch 6 | Batch: 26 | Loss: 6.6301
Epoch 6 | Batch: 27 | Loss: 10.4206
Epoch 6 | Batch: 28 | Loss: 11.2375
Epoch 6 | Batch:

Epoch 11 | Batch: 1 | Loss: 6.6031
Epoch 11 | Batch: 2 | Loss: 8.7012
Epoch 11 | Batch: 3 | Loss: 8.3402
Epoch 11 | Batch: 4 | Loss: 9.4734
Epoch 11 | Batch: 5 | Loss: 8.7822
Epoch 11 | Batch: 6 | Loss: 7.7788
Epoch 11 | Batch: 7 | Loss: 11.0699
Epoch 11 | Batch: 8 | Loss: 10.1990
Epoch 11 | Batch: 9 | Loss: 6.1395
Epoch 11 | Batch: 10 | Loss: 9.5661
Epoch 11 | Batch: 11 | Loss: 10.3328
Epoch 11 | Batch: 12 | Loss: 9.4929
Epoch 11 | Batch: 13 | Loss: 8.7162
Epoch 11 | Batch: 14 | Loss: 7.2514
Epoch 11 | Batch: 15 | Loss: 10.7851
Epoch 11 | Batch: 16 | Loss: 8.9133
Epoch 11 | Batch: 17 | Loss: 7.6190
Epoch 11 | Batch: 18 | Loss: 10.0832
Epoch 11 | Batch: 19 | Loss: 6.8038
Epoch 11 | Batch: 20 | Loss: 11.4843
Epoch 11 | Batch: 21 | Loss: 10.4211
Epoch 11 | Batch: 22 | Loss: 9.0028
Epoch 11 | Batch: 23 | Loss: 7.8185
Epoch 11 | Batch: 24 | Loss: 7.6836
Epoch 11 | Batch: 25 | Loss: 8.9659
Epoch 11 | Batch: 26 | Loss: 5.6862
Epoch 11 | Batch: 27 | Loss: 9.8969
Epoch 11 | Batch: 28 | Loss: 7

Epoch 15 | Batch: 35 | Loss: 9.3820
Epoch 15 | Batch: 36 | Loss: 4.2398
Epoch 15 | Batch: 37 | Loss: 5.0888
Epoch 15 | Batch: 38 | Loss: 11.3517
Epoch 15 | Batch: 39 | Loss: 7.1796
Epoch 15 | Batch: 40 | Loss: 9.3332
Epoch 15 | Batch: 41 | Loss: 7.7795
Epoch 15 | Batch: 42 | Loss: 6.7983
Epoch 15 | Batch: 43 | Loss: 8.0369
Epoch 15 | Batch: 44 | Loss: 10.9139
Epoch 15 | Batch: 45 | Loss: 9.1246
Epoch 15 | Batch: 46 | Loss: 7.1844
Epoch 15 | Batch: 47 | Loss: 5.0132
Epoch 15 | Batch: 48 | Loss: 3.3937
Mean 7.555925558010737
Epoch 16 | Batch: 1 | Loss: 9.9050
Epoch 16 | Batch: 2 | Loss: 7.9976
Epoch 16 | Batch: 3 | Loss: 6.0778
Epoch 16 | Batch: 4 | Loss: 9.1025
Epoch 16 | Batch: 5 | Loss: 12.5441
Epoch 16 | Batch: 6 | Loss: 7.3381
Epoch 16 | Batch: 7 | Loss: 11.5941
Epoch 16 | Batch: 8 | Loss: 7.8599
Epoch 16 | Batch: 9 | Loss: 7.3614
Epoch 16 | Batch: 10 | Loss: 6.9157
Epoch 16 | Batch: 11 | Loss: 6.9432
Epoch 16 | Batch: 12 | Loss: 7.4662
Epoch 16 | Batch: 13 | Loss: 5.1752
Epoch 16 |

Epoch 20 | Batch: 21 | Loss: 5.2170
Epoch 20 | Batch: 22 | Loss: 16.6067
Epoch 20 | Batch: 23 | Loss: 8.1575
Epoch 20 | Batch: 24 | Loss: 8.5814
Epoch 20 | Batch: 25 | Loss: 5.5168
Epoch 20 | Batch: 26 | Loss: 7.5098
Epoch 20 | Batch: 27 | Loss: 6.3546
Epoch 20 | Batch: 28 | Loss: 8.4551
Epoch 20 | Batch: 29 | Loss: 7.5917
Epoch 20 | Batch: 30 | Loss: 10.5316
Epoch 20 | Batch: 31 | Loss: 5.4275
Epoch 20 | Batch: 32 | Loss: 5.3309
Epoch 20 | Batch: 33 | Loss: 3.6276
Epoch 20 | Batch: 34 | Loss: 10.0601
Epoch 20 | Batch: 35 | Loss: 5.2908
Epoch 20 | Batch: 36 | Loss: 10.8357
Epoch 20 | Batch: 37 | Loss: 8.3089
Epoch 20 | Batch: 38 | Loss: 3.9996
Epoch 20 | Batch: 39 | Loss: 12.9024
Epoch 20 | Batch: 40 | Loss: 9.9496
Epoch 20 | Batch: 41 | Loss: 5.5223
Epoch 20 | Batch: 42 | Loss: 9.6441
Epoch 20 | Batch: 43 | Loss: 7.3768
Epoch 20 | Batch: 44 | Loss: 8.9952
Epoch 20 | Batch: 45 | Loss: 13.9103
Epoch 20 | Batch: 46 | Loss: 9.4529
Epoch 20 | Batch: 47 | Loss: 6.6343
Epoch 20 | Batch: 48 |

...

Epoch 2979 | Batch: 22 | Loss: 1.6009
Epoch 2979 | Batch: 23 | Loss: 0.6062
Epoch 2979 | Batch: 24 | Loss: 4.9508
Epoch 2979 | Batch: 25 | Loss: 1.0317
Epoch 2979 | Batch: 26 | Loss: 4.1264
Epoch 2979 | Batch: 27 | Loss: 0.5827
Epoch 2979 | Batch: 28 | Loss: 1.1072
Epoch 2979 | Batch: 29 | Loss: 8.3612
Epoch 2979 | Batch: 30 | Loss: 3.3623
Epoch 2979 | Batch: 31 | Loss: 0.5877
Epoch 2979 | Batch: 32 | Loss: 0.9888
Epoch 2979 | Batch: 33 | Loss: 2.4383
Epoch 2979 | Batch: 34 | Loss: 1.1435
Epoch 2979 | Batch: 35 | Loss: 4.6533
Epoch 2979 | Batch: 36 | Loss: 1.2678
Epoch 2979 | Batch: 37 | Loss: 2.7764
Epoch 2979 | Batch: 38 | Loss: 1.5475
Epoch 2979 | Batch: 39 | Loss: 0.6458
Epoch 2979 | Batch: 40 | Loss: 1.3706
Epoch 2979 | Batch: 41 | Loss: 0.5154
Epoch 2979 | Batch: 42 | Loss: 1.7833
Epoch 2979 | Batch: 43 | Loss: 3.1172
Epoch 2979 | Batch: 44 | Loss: 2.4014
Epoch 2979 | Batch: 45 | Loss: 1.3793
Epoch 2979 | Batch: 46 | Loss: 0.6942
Epoch 2979 | Batch: 47 | Loss: 2.1245
Epoch 2979 |

Epoch 2984 | Batch: 1 | Loss: 0.9549
Epoch 2984 | Batch: 2 | Loss: 0.6355
Epoch 2984 | Batch: 3 | Loss: 2.0329
Epoch 2984 | Batch: 4 | Loss: 1.6590
Epoch 2984 | Batch: 5 | Loss: 4.2287
Epoch 2984 | Batch: 6 | Loss: 0.3997
Epoch 2984 | Batch: 7 | Loss: 2.2797
Epoch 2984 | Batch: 8 | Loss: 1.7254
Epoch 2984 | Batch: 9 | Loss: 0.0365
Epoch 2984 | Batch: 10 | Loss: 2.9726
Epoch 2984 | Batch: 11 | Loss: 1.4594
Epoch 2984 | Batch: 12 | Loss: 5.4339
Epoch 2984 | Batch: 13 | Loss: 0.8053
Epoch 2984 | Batch: 14 | Loss: 0.3698
Epoch 2984 | Batch: 15 | Loss: 4.9727
Epoch 2984 | Batch: 16 | Loss: 2.4694
Epoch 2984 | Batch: 17 | Loss: 3.7699
Epoch 2984 | Batch: 18 | Loss: 0.7418
Epoch 2984 | Batch: 19 | Loss: 1.9202
Epoch 2984 | Batch: 20 | Loss: 1.4105
Epoch 2984 | Batch: 21 | Loss: 1.9584
Epoch 2984 | Batch: 22 | Loss: 4.3590
Epoch 2984 | Batch: 23 | Loss: 2.3587
Epoch 2984 | Batch: 24 | Loss: 0.1762
Epoch 2984 | Batch: 25 | Loss: 1.4077
Epoch 2984 | Batch: 26 | Loss: 1.9196
Epoch 2984 | Batch: 2

Epoch 2988 | Batch: 31 | Loss: 3.7000
Epoch 2988 | Batch: 32 | Loss: 0.7529
Epoch 2988 | Batch: 33 | Loss: 0.9344
Epoch 2988 | Batch: 34 | Loss: 2.7903
Epoch 2988 | Batch: 35 | Loss: 0.6302
Epoch 2988 | Batch: 36 | Loss: 0.5127
Epoch 2988 | Batch: 37 | Loss: 2.2828
Epoch 2988 | Batch: 38 | Loss: 3.9459
Epoch 2988 | Batch: 39 | Loss: 1.1734
Epoch 2988 | Batch: 40 | Loss: 0.9197
Epoch 2988 | Batch: 41 | Loss: 0.7294
Epoch 2988 | Batch: 42 | Loss: 4.0112
Epoch 2988 | Batch: 43 | Loss: 3.6663
Epoch 2988 | Batch: 44 | Loss: 1.5778
Epoch 2988 | Batch: 45 | Loss: 1.6227
Epoch 2988 | Batch: 46 | Loss: 1.7287
Epoch 2988 | Batch: 47 | Loss: 5.7067
Epoch 2988 | Batch: 48 | Loss: 0.2090
Mean 1.664452401145051
Epoch 2989 | Batch: 1 | Loss: 4.0373
Epoch 2989 | Batch: 2 | Loss: 4.2158
Epoch 2989 | Batch: 3 | Loss: 1.4946
Epoch 2989 | Batch: 4 | Loss: 1.5431
Epoch 2989 | Batch: 5 | Loss: 2.1460
Epoch 2989 | Batch: 6 | Loss: 1.6094
Epoch 2989 | Batch: 7 | Loss: 2.2433
Epoch 2989 | Batch: 8 | Loss: 0.37

Epoch 2993 | Batch: 5 | Loss: 2.7651
Epoch 2993 | Batch: 6 | Loss: 0.3058
Epoch 2993 | Batch: 7 | Loss: 3.0031
Epoch 2993 | Batch: 8 | Loss: 0.8880
Epoch 2993 | Batch: 9 | Loss: 2.6879
Epoch 2993 | Batch: 10 | Loss: 4.4232
Epoch 2993 | Batch: 11 | Loss: 0.4624
Epoch 2993 | Batch: 12 | Loss: 2.3373
Epoch 2993 | Batch: 13 | Loss: 0.7770
Epoch 2993 | Batch: 14 | Loss: 1.1721
Epoch 2993 | Batch: 15 | Loss: 1.9002
Epoch 2993 | Batch: 16 | Loss: 1.0139
Epoch 2993 | Batch: 17 | Loss: 0.2024
Epoch 2993 | Batch: 18 | Loss: 0.1385
Epoch 2993 | Batch: 19 | Loss: 1.3482
Epoch 2993 | Batch: 20 | Loss: 1.3942
Epoch 2993 | Batch: 21 | Loss: 0.6713
Epoch 2993 | Batch: 22 | Loss: 4.9691
Epoch 2993 | Batch: 23 | Loss: 1.4432
Epoch 2993 | Batch: 24 | Loss: 1.8911
Epoch 2993 | Batch: 25 | Loss: 2.1568
Epoch 2993 | Batch: 26 | Loss: 4.0513
Epoch 2993 | Batch: 27 | Loss: 0.9550
Epoch 2993 | Batch: 28 | Loss: 5.4519
Epoch 2993 | Batch: 29 | Loss: 0.6715
Epoch 2993 | Batch: 30 | Loss: 2.3999
Epoch 2993 | Batc

Epoch 2997 | Batch: 32 | Loss: 0.8912
Epoch 2997 | Batch: 33 | Loss: 1.0700
Epoch 2997 | Batch: 34 | Loss: 2.1713
Epoch 2997 | Batch: 35 | Loss: 1.9059
Epoch 2997 | Batch: 36 | Loss: 0.7870
Epoch 2997 | Batch: 37 | Loss: 1.9415
Epoch 2997 | Batch: 38 | Loss: 2.1530
Epoch 2997 | Batch: 39 | Loss: 0.4556
Epoch 2997 | Batch: 40 | Loss: 3.8079
Epoch 2997 | Batch: 41 | Loss: 2.2685
Epoch 2997 | Batch: 42 | Loss: 1.7855
Epoch 2997 | Batch: 43 | Loss: 1.7163
Epoch 2997 | Batch: 44 | Loss: 1.9289
Epoch 2997 | Batch: 45 | Loss: 1.0584
Epoch 2997 | Batch: 46 | Loss: 1.7886
Epoch 2997 | Batch: 47 | Loss: 0.9622
Epoch 2997 | Batch: 48 | Loss: 0.3103
Mean 1.6968683979163568
Epoch 2998 | Batch: 1 | Loss: 2.0230
Epoch 2998 | Batch: 2 | Loss: 0.6259
Epoch 2998 | Batch: 3 | Loss: 1.2604
Epoch 2998 | Batch: 4 | Loss: 0.5092
Epoch 2998 | Batch: 5 | Loss: 0.0551
Epoch 2998 | Batch: 6 | Loss: 1.1464
Epoch 2998 | Batch: 7 | Loss: 0.2879
Epoch 2998 | Batch: 8 | Loss: 2.1387
Epoch 2998 | Batch: 9 | Loss: 1.77

Mean 1.9 / Batch(=16) 3000 epochs lr = 0.08
NN shape
            nn.Linear(8,12),
            nn.Sigmoid(),
            nn.Linear(12,8),
            nn.Sigmoid(),
            nn.Linear(8,1),
            nn.Sigmoid()